# T5 model classification training

## Links:
- Tensorboard training: https://tensorboard.dev/experiment/CgaWd9pATZeuquRT7TZp7w/#scalars
- Huggingface dataset edited: https://huggingface.co/datasets/Zombely/sst2-project-dataset
- Huggingface Trained model: https://huggingface.co/Zombely/t5-model
- Huggingface Tokenizer: https://huggingface.co/Zombely/t5-tokenizer

In [1]:
!pip install datasets transformers sentencepiece

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 462.8/462.8 KB 8.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.3/6.3 MB 66.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 49.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 190.3/190.3 KB 14.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 213.0/213.0 KB 10.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 132.0/132.0 KB 10.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.6/7.6 MB 72.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 140.6/140.6 KB 10.8 MB/s eta 0:00:00
  Attempting uninstall: urllib3
    Found existing installation: urllib3 1.24.3
    Uninstalling urllib3-1.24.3:
      Successfully uninstalled urllib3-1.24.3


In [2]:
from datasets import load_dataset
import torch
from transformers import T5ForConditionalGeneration, T5Tokenizer, TrainingArguments, Trainer
from sklearn.metrics import accuracy_score, precision_recall_fscore_support
import tensorflow as tf
from torch.utils.data import DataLoader, RandomSampler, SequentialSampler, TensorDataset
import random
import time
import numpy as np
import datetime
import sklearn
from tqdm.notebook import tqdm
import os

## Load data and transform dataset

In [3]:
def load_and_process_dataset():
    dataset = load_dataset("sst2")
    dataset.remove_columns('idx')
    del dataset['test']
    dataset['test'] = dataset['validation']
    del dataset['validation']
    split_dataset = dataset['train'].train_test_split(test_size=1600)
    dataset['train'] = split_dataset['train']
    dataset['validation'] = split_dataset['test']
    return dataset

In [29]:
dataset = load_and_process_dataset()
dataset

  0%|          | 0/3 [00:00<?, ?it/s]

DatasetDict({
    train: Dataset({
        features: ['idx', 'sentence', 'label'],
        num_rows: 65749
    })
    test: Dataset({
        features: ['idx', 'sentence', 'label'],
        num_rows: 872
    })
    validation: Dataset({
        features: ['idx', 'sentence', 'label'],
        num_rows: 1600
    })
})

In [5]:
for key in dataset.keys():
  dataset[key] = dataset[key].map(lambda x: {'source_text': f"sentiment-analysis: {x['sentence']}", 'target_text': 'positive' if x['label'] else 'negative'}).remove_columns(['idx', 'sentence', 'label'])

  0%|          | 0/65749 [00:00<?, ?ex/s]

  0%|          | 0/872 [00:00<?, ?ex/s]

  0%|          | 0/1600 [00:00<?, ?ex/s]

In [6]:
train = dataset['train']
validation = dataset['validation']
test = dataset['test']

In [7]:
dataset['train'][0]

{'source_text': 'sentiment-analysis: smart , sassy and exceptionally charming ',
 'target_text': 'positive'}

In [8]:
tokenizer = T5Tokenizer.from_pretrained("t5-small")
model = T5ForConditionalGeneration.from_pretrained("t5-small")

/usr/local/lib/python3.8/dist-packages/transformers/models/t5/tokenization_t5.py:163: FutureWarning: This tokenizer was incorrectly instantiated with a model max length of 512 which will be corrected in Transformers v5.
For now, this behavior is kept to avoid breaking backwards compatibility when padding/encoding with `truncation is True`.
- Be aware that you SHOULD NOT rely on t5-small automatically truncating your input to 512 when padding/encoding.
- If you want to encode/pad to sequences longer than 512 you can either instantiate this tokenizer with `model_max_length` or pass `max_length` when encoding/padding.
- To avoid this warning, please instantiate this tokenizer with `model_max_length` set to your preferred value.
  warnings.warn(


In [9]:
model.cuda();

In [10]:
def tokenize(dataset):
  input_ids = []
  target_ids = []
  attention_masks = []
  for row in dataset:
    encoding = tokenizer.encode_plus(
      row['source_text'],
      padding="max_length",
      max_length=86,
      truncation=True,
      add_special_tokens = True,
      return_attention_mask = True,
      return_tensors="pt"
    )
    target_encoding = tokenizer.encode_plus(
      row['target_text'],
      padding="max_length",
      max_length=2,
      truncation=True,
      add_special_tokens = True,
      return_attention_mask = True,
      return_tensors="pt",
    )
    input_ids.append(encoding['input_ids'])
    target_ids.append(target_encoding['input_ids'])
    attention_masks.append(encoding['attention_mask'])
  return TensorDataset(torch.cat(input_ids, dim=0), torch.cat(attention_masks, dim=0), torch.cat(target_ids, dim=0))


In [11]:
train_tokenized = tokenize(train)
validation_tokenized = tokenize(validation)
test_tokenized = tokenize(test)

In [12]:
batch_size = 32

train_dataloader = DataLoader(
            train_tokenized,
            sampler = RandomSampler(train_tokenized),
            batch_size = batch_size
        )

validation_dataloader = DataLoader(
            validation_tokenized,
            sampler = SequentialSampler(validation_tokenized),
            batch_size = batch_size
        )

test_dataloader = DataLoader(
            test_tokenized,
            sampler = SequentialSampler(test_tokenized),
            batch_size = batch_size
        )

# Main model training class

In [13]:
class T5Model:
  def __init__(self, model, tokenizer, train_dataloader, val_dataloader, logs_dir_path, seed=42, epochs=3, lr=1e-4, eps=1e-8):
    self.model = model
    self.tokenizer = tokenizer
    self.train_dataloader = train_dataloader
    self.val_dataloader = val_dataloader
    self.seed=seed
    self.epochs = epochs
    self.learning_rate = lr
    self.eps = eps
    self.logs_dir_path = logs_dir_path
    self.device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
    self.optimizer = torch.optim.AdamW(model.parameters(), lr = lr, eps = eps)
    self.tensorboard_writter()
    self.init_seed()

  def init_seed(self):
    random.seed(self.seed)
    np.random.seed(self.seed)
    torch.manual_seed(self.seed)
    torch.cuda.manual_seed_all(self.seed)

  def tensorboard_writter(self):
    if not os.path.exists(self.logs_dir_path):
      os.mkdir(self.logs_dir_path)
    self.summary_writer = tf.summary.create_file_writer(self.logs_dir_path)

  def compute_metrics(self, target, preds):
      return sklearn.metrics.accuracy_score(target, preds)

  def _train(self, epoch_number):
    print(f"Training epoch: {epoch_number}")
    self.model.train()
    train_accuracy_total = 0
    pbar = tqdm(self.train_dataloader, total=len(self.train_dataloader))
    for step, batch in enumerate(pbar):
        b_input_ids = batch[0].to(self.device)
        b_input_mask = batch[1].to(self.device)
        b_labels = batch[2].to(self.device)

        outputs = self.model(
            input_ids=b_input_ids,
            attention_mask=b_input_mask,
            labels=b_labels
        )

        gen_output = self.model.generate(
            input_ids = b_input_ids,
            attention_mask = b_input_mask, 
            max_length=3, 
            num_beams=2,
            repetition_penalty=2.5, 
            length_penalty=1.0, 
            early_stopping=True
        )

        preds = [self.tokenizer.decode(g, skip_special_tokens=True, clean_up_tokenization_spaces=True) for g in gen_output]
        target = [self.tokenizer.decode(t, skip_special_tokens=True, clean_up_tokenization_spaces=True) for t in b_labels]

        loss = outputs[0]
        self.optimizer.zero_grad()
        loss.backward()
        self.optimizer.step()

        accuracy = self.compute_metrics(target, preds)
        train_accuracy_total += accuracy
        pbar.set_description(f"Epoch {epoch_number+1}, step {step}, train loss {loss}, accuracy: {accuracy}")

        with self.summary_writer.as_default():
          tf.summary.scalar(name=f"Epoch: {epoch_number+1}, step/train_accuracy", data=accuracy ,step=step)
          tf.summary.scalar(name=f"Epoch: {epoch_number+1}, step/train_loss", data=loss.cpu().detach().numpy(), step=step)
        self.summary_writer.flush()
    print(f"Epoch: {epoch_number+1}, Average train accuracy: {train_accuracy_total/len(self.train_dataloader)}")

  def train(self):
    print(f"Starting training, epochs: {self.epochs}")
    for i in range(0, self.epochs):
      self._train(i)
      self.validate(i)
      
  def validate(self, epoch_number):
    print(f"Validation epoch: {epoch_number}")
    self.model.eval()
    val_accuracy_total = 0
    pbar_val = tqdm(self.val_dataloader, total=len(self.val_dataloader))
    for step, batch in enumerate(pbar_val):
        b_input_ids = batch[0].to(self.device)
        b_input_mask = batch[1].to(self.device)
        b_labels = batch[2].to(self.device)

        with torch.no_grad():        

          outputs = self.model(
            input_ids=b_input_ids,
            attention_mask=b_input_mask,
            labels=b_labels
          )

          loss = outputs[0]

          gen_output = self.model.generate(
            input_ids = b_input_ids,
            attention_mask = b_input_mask, 
            max_length=3, 
            num_beams=2,
            repetition_penalty=2.5, 
            length_penalty=1.0, 
            early_stopping=True
          )

          preds = [self.tokenizer.decode(g, skip_special_tokens=True, clean_up_tokenization_spaces=True) for g in gen_output]
          target = [self.tokenizer.decode(t, skip_special_tokens=True, clean_up_tokenization_spaces=True) for t in b_labels]

          accuracy_val = self.compute_metrics(target, preds)
          val_accuracy_total += accuracy_val
          pbar_val.set_description(f"Epoch {epoch_number+1}, val loss {loss}, accuracy: {accuracy_val}")

          with self.summary_writer.as_default():
            tf.summary.scalar(name=f"Epoch: {epoch_number+1}, step/val_accuracy", data=accuracy_val ,step=step)
            tf.summary.scalar(name=f"Epoch: {epoch_number+1}, step/val_loss", data=loss.cpu().detach().numpy(), step=step)
          self.summary_writer.flush()

    print(f"Epoch: {epoch_number+1}, Average validation accuracy: {val_accuracy_total/len(self.val_dataloader)}")

  def evaluate(self, test_dataloader):
    self.model.eval()
    total_test_acc = 0
    for batch in tqdm(test_dataloader, total=len(test_dataloader)):
        b_input_ids = batch[0].to(self.device)
        b_input_mask = batch[1].to(self.device)
        b_labels = batch[2].to(self.device)
        
        with torch.no_grad():        

          gen_output = self.model.generate(
            input_ids = b_input_ids,
            attention_mask = b_input_mask, 
            max_length=3, 
            num_beams=2,
            repetition_penalty=2.5, 
            length_penalty=1.0, 
            early_stopping=True
          )
            
        preds = [self.tokenizer.decode(g, skip_special_tokens=True, clean_up_tokenization_spaces=True) for g in gen_output]
        target = [self.tokenizer.decode(t, skip_special_tokens=True, clean_up_tokenization_spaces=True) for t in b_labels]
        total_test_acc += self.compute_metrics(preds, target)  
    print("Accuracy: ",total_test_acc / len(test_dataloader))
    

In [14]:
t5model = T5Model(model, tokenizer, train_dataloader, validation_dataloader, "./logs")
t5model.train()

Starting training, epochs: 3
Training epoch: 0


  0%|          | 0/2055 [00:00<?, ?it/s]

Epoch: 1, Average train accuracy: 0.8825947167188043
Validation epoch: 0


  0%|          | 0/50 [00:00<?, ?it/s]

Epoch: 1, Average validation accuracy: 0.926875
Training epoch: 1


...

Epoch: 2, Average validation accuracy: 0.936875
Training epoch: 2


  0%|          | 0/2055 [00:00<?, ?it/s]

Epoch: 3, Average train accuracy: 0.9391720252577916
Validation epoch: 2


  0%|          | 0/50 [00:00<?, ?it/s]

Epoch: 3, Average validation accuracy: 0.93875


In [15]:
t5model.evaluate(test_dataloader)

  0%|          | 0/28 [00:00<?, ?it/s]

Accuracy:  0.9129464285714286


In [16]:
!tensorboard dev upload --logdir logs --name t5-sst2

2023-02-13 11:49:46.367397: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /usr/lib64-nvidia
2023-02-13 11:49:46.367509: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer_plugin.so.7'; dlerror: libnvinfer_plugin.so.7: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /usr/lib64-nvidia
2023-02-13 11:49:46.367529: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Cannot dlopen some TensorRT libraries. If you would like to use Nvidia GPU with TensorRT, please make sure the missing libraries mentioned above are installed properly.

***** TensorBoard Uploader *****

This will upload your TensorBoard logs to https://tensorboard.dev/ from
the following directory:

logs

This TensorBoard will be vis

In [17]:
t5model.model.save_pretrained("./model")
t5model.tokenizer.save_pretrained("./model")


('./model/tokenizer_config.json',
 './model/special_tokens_map.json',
 './model/spiece.model',
 './model/added_tokens.json')

In [23]:
!zip -r /content/model model

  adding: model/ (stored 0%)
  adding: model/tokenizer_config.json (deflated 82%)
  adding: model/config.json (deflated 62%)
  adding: model/generation_config.json (deflated 29%)
  adding: model/pytorch_model.bin (deflated 8%)
  adding: model/special_tokens_map.json (deflated 86%)
  adding: model/spiece.model (deflated 48%)


In [27]:
!huggingface-cli login


    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|
    
    To login, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Token: 
Add token as git credential? (Y/n) y
Token is valid.
Cannot authenticate through git-credential as no helper is defined on your machine.
You might have to re-authenticate when pushing to the Hugging Face Hub.
Run the following command in your terminal in case you want to set the 'store' credential helper as d

In [33]:
t5model.model.push_to_hub("Zombely/t5-model")

Upload 1 LFS files:   0%|          | 0/1 [00:00<?, ?it/s]

pytorch_model.bin:   0%|          | 0.00/242M [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/Zombely/t5-model/commit/caab3e8d5523bc7309774f13f522fd6f06666b29', commit_message='Upload T5ForConditionalGeneration', commit_description='', oid='caab3e8d5523bc7309774f13f522fd6f06666b29', pr_url=None, pr_revision=None, pr_num=None)

In [34]:
t5model.tokenizer.push_to_hub("Zombely/t5-tokenizer")


spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

Upload 1 LFS files:   0%|          | 0/1 [00:00<?, ?it/s]

CommitInfo(commit_url='https://huggingface.co/Zombely/t5-tokenizer/commit/640998bd3d496cbd5266140fbeff873d07c0158e', commit_message='Upload tokenizer', commit_description='', oid='640998bd3d496cbd5266140fbeff873d07c0158e', pr_url=None, pr_revision=None, pr_num=None)